In [13]:
import pandas as pd

In [1]:
!pip install surprise

  Using cached https://files.pythonhosted.org/packages/61/de/e5cba8682201fcf9c3719a6fdda95693468ed061945493dea2dd37c5618b/surprise-0.1-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/4d/fc/cd4210b247d1dca421c25994740cbbf03c5e980e31881f10eaddf45fdab0/scikit-surprise-1.0.6.tar.gz
  Stored in directory: C:\Users\cahib\AppData\Local\pip\Cache\wheels\ec\c0\55\3a28eab06b53c220015063ebbdb81213cd3dcbb72c088251ec
Successfully built scikit-surprise


In [18]:
#load MovieLens data
movies = pd.read_csv('movies_prepared.csv', sep='\t',encoding='latin-1')

#load the netflix movie data
netflix_movies = pd.read_csv('netflix_movies.csv')

#review data
netflix_movies.head()

MovieID  YearOfRelease                         Title
0        1         2003.0               Dinosaur Planet
1        2         2004.0    Isle of Man TT 2004 Review
2        3         1997.0                     Character
3        4         1994.0  Paula Abdul's Get Up & Dance
4        5         2004.0      The Rise and Fall of ECW

In [19]:
movies.head()

Unnamed: 0  movie_id                        title  is_drama  is_comedy  \
0           0         0                    Toy Story         0          1   
1           1         1                      Jumanji         0          0   
2           2         2             Grumpier Old Men         0          1   
3           3         3            Waiting to Exhale         1          1   
4           4         4  Father of the Bride Part II         0          1   

   is_action  is_thriller  is_romance  is_horror  is_adventure  ...  is_crime  \
0          0            0           0          0             0  ...         0   
1          0            0           0          0             1  ...         0   
2          0            0           1          0             0  ...         0   
3          0            0           0          0             0  ...         0   
4          0            0           0          0             0  ...         0   

   is_war  is_documentary  is_musical  is_mystery  is_animation  is_fantasy  \
0       0               0           0           0             1           0   
1       0               0           0           0             0           1   
2       0               0           0           0             0           0   
3       0               0           0           0             0           0   
4       0               0           0           0             0           0   

   is_western  is_filmnoir  year  
0           0            0  1995  
1           0            0  1995  
2           0            0  1995  
3           0            0  1995  
4           0            0  1995  

[5 rows x 22 columns]

In [20]:
#drop the release year column
netflix_movies.drop('YearOfRelease', inplace = True, axis = 1)

In [21]:
#review data
netflix_movies.head()

MovieID                         Title
0        1               Dinosaur Planet
1        2    Isle of Man TT 2004 Review
2        3                     Character
3        4  Paula Abdul's Get Up & Dance
4        5      The Rise and Fall of ECW

With the Netflix movie data now loaded, we will first count the number of titles within that dataset that overlap with titles within the MovieLens dataset.

In [32]:
from tqdm import tqdm_notebook 

def FindOverlap(dfcol):
    movie_overlap = 0

    for title in tqdm_notebook(movies.title):
        try:
            dfcol.loc[dfcol == title].index[0]
            movie_overlap += 1
        except:
            pass
        
    print("We found {0} of {1} ({2:.3f}) values within this database".format(movie_overlap, movies.title.size, movie_overlap/movies.title.size))

In [30]:
FindOverlap(netflix_movies.Title)


We found 2076 of 3883 (0.535) values within the Netflix database


The Netflix dataset has data on ~50% of the movies also contained within the Netflix database.  Knowing this, we first built in an additional index column into the netflix_movies DataFrame that gives the MovieLens index for a given film in the Netflix database.

In [25]:
from tqdm import tqdm_notebook

def AddMovieLensIndex():
    #initalize new column with easy to spot placeholder value
    netflix_movies['movieLensIndex'] = -1
    skip_count = 0
    #loop and add in MovieLens index to new column
    for index, title in tqdm_notebook(enumerate(movies.title)):
        try:
            netflix_index = netflix_movies.loc[netflix_movies.Title == title].index[0]
            netflix_movies.movieLensIndex.iloc[netflix_index] = index
        except:
            skip_count += 1
        
    return skip_count

In [26]:
#run the function
AddMovieLensIndex()

1807

In [100]:
netflix_movies.head()

MovieID                         Title  movieLensIndex
0        1               Dinosaur Planet              -1
1        2    Isle of Man TT 2004 Review              -1
2        3                     Character            1791
3        4  Paula Abdul's Get Up & Dance              -1
4        5      The Rise and Fall of ECW              -1

With the matches now identified and marked, we can push the matched film names into a new DataFrame.

In [103]:
netflix_matched = netflix_movies[netflix_movies.movieLensIndex != -1].copy()

In [104]:
netflix_matched.head()

MovieID             Title  movieLensIndex
2         3         Character            1791
15       16         Screamers              75
17       18  Immortal Beloved             246
54       55              Jade             130
56       57       Richard III              40

Now, we can filter down the Netflix reviews to only contain those movies matched in the MovieLens dataset.

In [111]:
#load the netflix review data
netflix_ratings = pd.read_csv('netflix_ratings.csv')

#review data
netflix_ratings.head()

MovieID   UserID  Rating
0       28  1392773     4.0
1       28  1990901     5.0
2       28   765331     3.0
3       28  1987434     4.0
4       28  2193455     4.0

We first note the current length of the Netflix ratings set, remove those values where the MovieID in the ratings file cannot be found in the clean version of the Netflix movies set, and then get the count of the remaining values.

In [114]:
netflix_ratings.shape

(227773, 3)

In [115]:
netflix_ratings_clean = netflix_ratings[netflix_ratings['MovieID'].isin(netflix_matched.MovieID)]

In [116]:
netflix_ratings_clean.shape

(66295, 3)

With the data now stripped down to only those values that overlap the MovieLens dataset, we can reindex the UserID values in the reviews dataset so they are 0-indexed.  We extract the unique values contained in that column, and then use the same functions built to reindex the MovieLens film dataset to accomplish this task.

In [119]:
unique_userIDs = netflix_ratings_clean.UserID.unique()

In [121]:
def DatasetIndexExtract(dfcol):
    '''
    Accepts a column of a DataFrame.  Extracts the value and DataFrame index of that column,
    returning a dictionary of {value: index} that can be used to transform the index of the dataset to
    match the row indexing of the DataFrame.
    '''
    index_dict = {}
    for index, value in enumerate(dfcol):
        index_dict.update({value : index})
    return index_dict

In [124]:
from tqdm import tqdm_notebook

def DatasetReindex(dfcol,index_dict):
    '''
    Accepts a DataFrame column and a dictionary of {value:index} pairs.  Transforms the column
    to match the indexing of the underlying DataFrame.
    '''
    for index, value in tqdm_notebook(enumerate(dfcol)):
        try:
            dfcol.iloc[index] = index_dict[value]
        except:
            print("error at index ", index)

In [126]:
userID_dict = DatasetIndexExtract(unique_userIDs)
DatasetReindex(netflix_ratings_clean.UserID,userID_dict)













0it [00:00, ?it/s]C:\Users\cahib\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # Remove the CWD from sys.path while we load stuff.












2it [00:00, 16.04it/s]











4it [00:00, 16.36it/s]











6it [00:00, 16.67it/s]











8it [00:00, 16.70it/s]











10it [00:00, 17.13it/s]











12it [00:00, 17.55it/s]











14it [00:00, 17.94it/s]











16it [00:00, 18.02it/s]











18it [00:01, 18.18it/s]











20it [00:01, 17.64it/s]











22it [00:01, 16.83it/s]











24it [00:01, 16.92it/s]











26it [00:01, 17.10it/s]











28it [00:01, 17.47it/s]











30it [00:01, 17.69it/s]











32it [00:01, 17.75it/s]











34it [00:01, 17.34it/s]











36it [00:02, 17.74it/s]








964it [00:52, 18.75it/s]











966it [00:52, 18.34it/s]











968it [00:52, 18.31it/s]











970it [00:52, 18.56it/s]











972it [00:52, 18.46it/s]











974it [00:52, 18.34it/s]











976it [00:52, 18.26it/s]











978it [00:52, 18.15it/s]











980it [00:53, 17.19it/s]











982it [00:53, 17.09it/s]











984it [00:53, 17.41it/s]











986it [00:53, 17.55it/s]











988it [00:53, 17.75it/s]











990it [00:53, 17.94it/s]











992it [00:53, 18.42it/s]











994it [00:53, 18.62it/s]











996it [00:53, 18.76it/s]











998it [00:54, 18.75it/s]











1000it [00:54, 18.70it/s]











1002it [00:54, 18.61it/s]











1004it [00:54, 18.70it/s]











1006it [00:54, 18.35it/s]











1008it [00:54, 18.42it/s]











1010it [00:54, 18.21it/s]











1012it [00:54, 18.02it/s]











1014it [00:54, 18.03it/s]











1016it [00:55, 18.00it/s]











1018it [00:55, 17.7

1545it [01:21, 20.55it/s]











1548it [01:21, 20.07it/s]











1551it [01:21, 20.06it/s]











1554it [01:21, 19.90it/s]











1556it [01:22, 19.77it/s]











1558it [01:22, 19.74it/s]











1560it [01:22, 19.60it/s]











1563it [01:22, 20.05it/s]











1566it [01:22, 20.21it/s]











1569it [01:22, 20.44it/s]











1572it [01:22, 20.57it/s]











1575it [01:22, 20.45it/s]











1578it [01:23, 20.63it/s]











1581it [01:23, 20.83it/s]











1584it [01:23, 20.94it/s]











1587it [01:23, 21.05it/s]











1590it [01:23, 21.15it/s]











1593it [01:23, 21.01it/s]











1596it [01:23, 20.78it/s]











1599it [01:24, 20.77it/s]











1602it [01:24, 20.46it/s]











1605it [01:24, 19.66it/s]











1607it [01:24, 19.38it/s]











1610it [01:24, 19.73it/s]











1613it [01:24, 20.22it/s]











1616it [01:24, 20.42it/s]











1619it [01:25, 20.73it/s]











1

2596it [02:16, 16.77it/s]











2598it [02:16, 17.18it/s]











2600it [02:16, 17.71it/s]











2603it [02:16, 18.56it/s]











2606it [02:16, 19.24it/s]











2608it [02:16, 17.86it/s]











2610it [02:16, 17.55it/s]











2612it [02:17, 17.47it/s]











2614it [02:17, 17.69it/s]











2616it [02:17, 17.80it/s]











2618it [02:17, 17.37it/s]











2620it [02:17, 16.95it/s]











2622it [02:17, 15.95it/s]











2625it [02:17, 17.17it/s]











2627it [02:17, 17.31it/s]











2629it [02:18, 17.30it/s]











2631it [02:18, 16.91it/s]











2633it [02:18, 16.76it/s]











2635it [02:18, 16.42it/s]











2637it [02:18, 17.10it/s]











2639it [02:18, 17.74it/s]











2641it [02:18, 18.15it/s]











2644it [02:18, 18.65it/s]











2646it [02:19, 18.58it/s]











2648it [02:19, 18.53it/s]











2650it [02:19, 17.20it/s]











2652it [02:19, 17.09it/s]











2

3617it [03:10, 20.74it/s]











3620it [03:10, 20.92it/s]











3623it [03:10, 21.04it/s]











3626it [03:10, 21.13it/s]











3629it [03:10, 21.28it/s]











3632it [03:11, 21.39it/s]











3635it [03:11, 21.32it/s]











3638it [03:11, 21.24it/s]











3641it [03:11, 21.22it/s]











3644it [03:11, 21.39it/s]











3647it [03:11, 20.88it/s]











3650it [03:11, 20.93it/s]











3653it [03:12, 21.05it/s]











3656it [03:12, 21.27it/s]











3659it [03:12, 21.20it/s]











3662it [03:12, 21.28it/s]











3665it [03:12, 21.30it/s]











3668it [03:12, 21.32it/s]











3671it [03:12, 21.39it/s]











3674it [03:12, 21.06it/s]











3677it [03:13, 21.27it/s]











3680it [03:13, 21.09it/s]











3683it [03:13, 21.25it/s]











3686it [03:13, 21.43it/s]











3689it [03:13, 21.50it/s]











3692it [03:13, 21.59it/s]











3695it [03:13, 21.65it/s]











3

...

64461it [1:09:44, 16.21it/s]











64463it [1:09:44, 16.57it/s]











64465it [1:09:44, 16.99it/s]











64467it [1:09:44, 17.46it/s]











64469it [1:09:44, 18.02it/s]











64471it [1:09:44, 17.70it/s]











64473it [1:09:44, 16.82it/s]











64475it [1:09:44, 17.54it/s]











64478it [1:09:45, 18.39it/s]











64481it [1:09:45, 19.00it/s]











64483it [1:09:45, 18.66it/s]











64485it [1:09:45, 17.11it/s]











64487it [1:09:45, 16.20it/s]











64489it [1:09:45, 16.51it/s]











64491it [1:09:45, 15.92it/s]











64493it [1:09:45, 15.55it/s]











64495it [1:09:46, 15.26it/s]











64497it [1:09:46, 15.56it/s]











64499it [1:09:46, 16.04it/s]











64501it [1:09:46, 16.28it/s]











64503it [1:09:46, 16.95it/s]











64505it [1:09:46, 16.75it/s]











64507it [1:09:46, 16.49it/s]











64509it [1:09:46, 17.26it/s]











64511it [1:09:47, 17.63it/s]













64892it [1:10:08, 16.79it/s]











64894it [1:10:08, 16.94it/s]











64896it [1:10:08, 16.91it/s]











64898it [1:10:08, 17.38it/s]











64900it [1:10:08, 16.74it/s]











64902it [1:10:09, 16.57it/s]











64904it [1:10:09, 16.13it/s]











64906it [1:10:09, 15.99it/s]











64908it [1:10:09, 16.73it/s]











64910it [1:10:09, 16.89it/s]











64912it [1:10:09, 17.18it/s]











64914it [1:10:09, 17.53it/s]











64916it [1:10:09, 17.37it/s]











64918it [1:10:10, 16.95it/s]











64920it [1:10:10, 17.20it/s]











64922it [1:10:10, 17.36it/s]











64925it [1:10:10, 17.86it/s]











64927it [1:10:10, 17.36it/s]











64929it [1:10:10, 17.34it/s]











64931it [1:10:10, 16.72it/s]











64933it [1:10:10, 17.01it/s]











64935it [1:10:11, 17.41it/s]











64937it [1:10:11, 17.10it/s]











64939it [1:10:11, 17.56it/s]











64942it [1:10:11, 18.51it/s]













65312it [1:10:32, 16.94it/s]











65314it [1:10:32, 16.62it/s]











65316it [1:10:32, 15.74it/s]











65318it [1:10:33, 14.59it/s]











65320it [1:10:33, 14.26it/s]











65322it [1:10:33, 14.50it/s]











65324it [1:10:33, 14.32it/s]











65326it [1:10:33, 14.29it/s]











65328it [1:10:33, 14.27it/s]











65330it [1:10:33, 14.44it/s]











65332it [1:10:34, 14.22it/s]











65334it [1:10:34, 14.47it/s]











65336it [1:10:34, 14.61it/s]











65338it [1:10:34, 14.69it/s]











65340it [1:10:34, 14.83it/s]











65342it [1:10:34, 14.84it/s]











65344it [1:10:34, 14.65it/s]











65346it [1:10:35, 14.91it/s]











65348it [1:10:35, 14.71it/s]











65350it [1:10:35, 14.88it/s]











65352it [1:10:35, 14.68it/s]











65354it [1:10:35, 14.32it/s]











65356it [1:10:35, 14.41it/s]











65358it [1:10:35, 14.42it/s]











65360it [1:10:36, 14.39it/s]













65723it [1:11:01, 15.28it/s]











65725it [1:11:01, 15.36it/s]











65727it [1:11:01, 15.20it/s]











65729it [1:11:01, 15.13it/s]











65731it [1:11:01, 15.22it/s]











65733it [1:11:01, 15.12it/s]











65735it [1:11:02, 15.01it/s]











65737it [1:11:02, 15.29it/s]











65739it [1:11:02, 15.10it/s]











65741it [1:11:02, 15.06it/s]











65743it [1:11:02, 14.75it/s]











65745it [1:11:02, 15.18it/s]











65747it [1:11:02, 15.22it/s]











65749it [1:11:02, 15.68it/s]











65751it [1:11:03, 15.46it/s]











65753it [1:11:03, 15.85it/s]











65755it [1:11:03, 16.25it/s]











65757it [1:11:03, 15.92it/s]











65759it [1:11:03, 15.80it/s]











65761it [1:11:03, 15.50it/s]











65763it [1:11:03, 15.68it/s]











65765it [1:11:03, 15.90it/s]











65767it [1:11:04, 15.36it/s]











65769it [1:11:04, 15.24it/s]











65771it [1:11:04, 15.23it/s]













66133it [1:11:30, 13.19it/s]











66135it [1:11:30, 13.93it/s]











66137it [1:11:30, 13.48it/s]











66139it [1:11:30, 13.58it/s]











66141it [1:11:30, 14.00it/s]











66143it [1:11:30, 13.72it/s]











66145it [1:11:31, 13.42it/s]











66147it [1:11:31, 13.22it/s]











66149it [1:11:31, 13.24it/s]











66151it [1:11:31, 13.22it/s]











66153it [1:11:31, 13.40it/s]











66155it [1:11:31, 13.39it/s]











66157it [1:11:31, 13.44it/s]











66159it [1:11:32, 13.44it/s]











66161it [1:11:32, 14.04it/s]











66163it [1:11:32, 14.22it/s]











66165it [1:11:32, 14.31it/s]











66167it [1:11:32, 15.40it/s]











66169it [1:11:32, 15.37it/s]











66171it [1:11:32, 15.41it/s]











66173it [1:11:32, 15.25it/s]











66175it [1:11:33, 15.24it/s]











66177it [1:11:33, 15.72it/s]











66179it [1:11:33, 16.01it/s]











66181it [1:11:33, 16.21it/s]













In [128]:
#save the clean files to CSV
netflix_ratings_clean.to_csv("netflix_ratings_clean.csv")
netflix_matched.to_csv("netflix_movies_clean.csv")